In [1]:
import pandas as pd
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from xgboost import XGBRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import cross_val_score
from lightgbm import LGBMRegressor
import matplotlib.pyplot as plt
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.model_selection import GridSearchCV
import lightgbm as lgb
import seaborn as sns
from sklearn import tree
import lightgbm as lgb
from xgboost import XGBClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB, MultinomialNB, BernoulliNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.ensemble import VotingClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix, classification_report, mean_squared_error, r2_score
from sklearn.utils import class_weight
from sklearn.neural_network import MLPClassifier

import warnings
warnings.filterwarnings("ignore")

# Import data

In [2]:
data = pd.read_csv('option_train.csv')

In [3]:
data.head()

Value           S      K       tau        r     BS
0  21.670404  431.623898  420.0  0.341270  0.03013  Under
1   0.125000  427.015526  465.0  0.166667  0.03126   Over
2  20.691244  427.762336  415.0  0.265873  0.03116  Under
3   1.035002  451.711658  460.0  0.063492  0.02972   Over
4  39.553020  446.718974  410.0  0.166667  0.02962  Under

Encode BS column - 1 is Over, 0 is Under

In [4]:
data['BS_encode'] = [1 if i == 'Over' else 0 for i in data['BS']]

In [5]:
data.shape

(1680, 7)

# Data filtering

## Drop 2 records that has null values

In [6]:
data.dropna(axis=0, inplace = True)

## Drop 3 outliers

In [7]:
data.describe()

Value            S            K          tau            r  \
count  1678.000000  1678.000000  1678.000000  1678.000000  1678.000000   
mean     15.075855   440.645020   438.241955     0.437643     0.030235   
std      14.039793    13.132362    23.408989     7.059657     0.000558   
min       0.125000     0.000000   375.000000     0.003968     0.029510   
25%       2.255001   433.869588   420.000000     0.119048     0.029820   
50%      11.235294   442.579723   440.000000     0.202381     0.030130   
75%      25.747434   447.320414   455.000000     0.285714     0.030540   
max      60.149367   455.880619   500.000000   250.000000     0.031880   

         BS_encode  
count  1678.000000  
mean      0.436234  
std       0.496065  
min       0.000000  
25%       0.000000  
50%       0.000000  
75%       1.000000  
max       1.000000

In [8]:
data.sort_values(by = 'tau',ascending = False)

Value           S      K         tau        r     BS  BS_encode
12     2.315001  448.688109  470.0  250.000000  0.03013   Over          1
33     2.565000  445.042240  455.0  146.000000  0.03003   Over          1
756   39.403943  451.221255  420.0    0.392857  0.03044  Under          0
1538  52.850633  451.221255  405.0    0.392857  0.03044  Under          0
700    3.440000  451.221255  475.0    0.392857  0.03044   Over          1
...         ...         ...    ...         ...      ...    ...        ...
1585  13.746462  433.302407  420.0    0.007937  0.02972  Under          0
1401   0.940008  447.891299  450.0    0.007937  0.03044  Under          0
1267   2.565006  431.949649  430.0    0.003968  0.02951  Under          0
1337   0.160004  431.949649  435.0    0.003968  0.02951   Over          1
1016   2.315000  451.916200  450.0    0.003968  0.03013   Over          1

[1678 rows x 7 columns]

In [9]:
data.sort_values(by = 'S',ascending = True)

Value           S      K       tau        r     BS  BS_encode
879    4.125000    0.000000  455.0  0.170635  0.03003   Over          1
1316   1.875007  425.472331  450.0  0.277778  0.03126   Over          1
1147   0.315004  425.472331  470.0  0.277778  0.03126   Over          1
780    3.035000  425.472331  445.0  0.277778  0.03126   Over          1
835   54.589484  425.472331  375.0  0.277778  0.03126  Under          0
...         ...         ...    ...       ...      ...    ...        ...
871   21.698269  455.880619  435.0  0.035714  0.03044  Under          0
1259  31.562404  455.880619  425.0  0.035714  0.03044  Under          0
1571   3.690000  455.880619  455.0  0.035714  0.03044   Over          1
663   36.496971  455.880619  420.0  0.035714  0.03044  Under          0
1218  12.024135  455.880619  445.0  0.035714  0.03044  Under          0

[1678 rows x 7 columns]

In [10]:
data.drop([12,33,879], inplace = True)

# Z-Scaling before building the models

In [50]:
stdx = StandardScaler()
stdy = StandardScaler()
X = data[['S','K','tau','r']]
y_value = data['Value']
y_BS = data['BS_encode']
X_z = stdx.fit_transform(data[['S','K','tau','r']])
y_z = (stdy.fit_transform(data[['Value']])).reshape(-1)

In [12]:
print(X_z.shape)
print(y_z.shape)
print(y_BS.shape)

(1675, 4)
(1675,)
(1675,)


# Method 1

## Regression Models

In [13]:
X_train, X_test, y_train, y_test = train_test_split(X_z, y_z, test_size = .2, random_state = 20)

### Linear Regression

There is no hyperparameter that can be tuned to improve the r2

In [14]:
kf5 = KFold(n_splits = 5, shuffle = True)

LR = LinearRegression()
cv = cross_val_score(LR, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

LR.fit(X_train, y_train)
y_pred = LR.predict(X_test)
print(LR.score(X_test, y_test))
print(mean_squared_error(y_test, y_pred))

[0.90212625 0.92244118 0.91256095 0.90289656 0.91414912] mean:  0.9108348116723907
0.9113948379740099
0.08698368333898136


### Decision Tree

In [15]:
kf5 = KFold(n_splits = 5, shuffle = True)
DT_param = {'criterion' : ['squared_error','friedman_mse','absolute_error','poisson'], 
            'splitter' : ['best','random'],
             'max_depth': list(range(2,21,2))+[None],
             'min_samples_split'  : [2,5,10,20,50],
             'min_samples_leaf'  : [1,5,10]}

DT = DecisionTreeRegressor()
DT_cv = GridSearchCV(DT, DT_param, cv = kf5, refit=True, verbose=3)
DT_cv.fit(X_train, y_train)
print(DT_cv.best_score_)
print(DT_cv.best_params_)

Fitting 5 folds for each of 1320 candidates, totalling 6600 fits
[CV 1/5] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.774 total time=   0.0s
[CV 2/5] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.800 total time=   0.0s
[CV 3/5] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.810 total time=   0.0s
[CV 4/5] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.837 total time=   0.0s
[CV 5/5] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.823 total time=   0.0s
[CV 1/5] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=random;, score=0.100 total time=   0.0s
[CV 2/5] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitte

In [16]:
DT = DecisionTreeRegressor(criterion = 'absolute_error', max_depth = 18, min_samples_leaf = 1, min_samples_split = 2, splitter = 'random')
cv = cross_val_score(DT, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

DT.fit(X_train, y_train)
y_pred = DT.predict(X_test)
print(DT.score(X_test, y_test))
print(mean_squared_error(y_test, y_pred))

[0.98612109 0.98414796 0.98394745 0.98781639 0.98957665] mean:  0.9863219059218565
0.9876794732314278
0.0120950605416485


### Random Forest

In [19]:
kf5 = KFold(n_splits = 5, shuffle = True)
RF_param = {'n_estimators' : [10, 50, 100, 150, 200], 
            'criterion': ['mse', 'mae', 'poisson'],
             'max_depth': list(range(2,11,2))+[None],
             'min_samples_split'  : [2,5,10,20],
             'min_samples_leaf'  : [1,5,10]}

RF = RandomForestRegressor()
RF_cv = GridSearchCV(RF, RF_param, cv = kf5, refit=True, verbose=3)
RF_cv.fit(X_train, y_train)
print(RF_cv.best_score_)
print(RF_cv.best_params_)

Fitting 5 folds for each of 1080 candidates, totalling 5400 fits
[CV 1/5] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.825 total time=   0.0s
[CV 2/5] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.834 total time=   0.0s
[CV 3/5] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.819 total time=   0.0s
[CV 4/5] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.855 total time=   0.0s
[CV 5/5] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.821 total time=   0.0s
[CV 1/5] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=50;, score=0.828 total time=   0.0s
[CV 2/5] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=50;, score=0.835 total time=   0.0s
[CV 3/5] END crite

In [22]:
RF = RandomForestRegressor(criterion = 'mse', max_depth = None, min_samples_leaf = 1, min_samples_split = 2, n_estimators = 100)
cv = cross_val_score(RF, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

RF.fit(X_train, y_train)
y_pred = RF.predict(X_test)
print(RF.score(X_test, y_test))
print(mean_squared_error(y_test, y_pred))

[0.99337713 0.99523641 0.99443084 0.9959725  0.99397311] mean:  0.9945979983130722
0.9956792537531669
0.004241676384637454


### Gradient Boosting Tree

In [23]:
kf5 = KFold(n_splits = 5, shuffle = True)
GB_param = {'n_estimators' : [10, 20, 50, 100, 150, 200, 500, 800], 
            'learning_rate' : [0.1, 0.01],
            'criterion' : ['friedman_mse', 'mse', 'mae'],
             'max_depth': [3, 4, 5, 10, None],
             'min_samples_split'  : [2,5,10],
             'min_samples_leaf'  : [1,5,10]}

GB = GradientBoostingRegressor()
GB_cv = GridSearchCV(GB, GB_param, cv = kf5, refit=True, verbose=3)
GB_cv.fit(X_train, y_train)
print(GB_cv.best_score_)
print(GB_cv.best_params_)

Fitting 5 folds for each of 2160 candidates, totalling 10800 fits
[CV 1/5] END criterion=friedman_mse, learning_rate=0.1, max_depth=3, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.819 total time=   0.0s
[CV 2/5] END criterion=friedman_mse, learning_rate=0.1, max_depth=3, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.823 total time=   0.0s
[CV 3/5] END criterion=friedman_mse, learning_rate=0.1, max_depth=3, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.809 total time=   0.0s
[CV 4/5] END criterion=friedman_mse, learning_rate=0.1, max_depth=3, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.827 total time=   0.0s
[CV 5/5] END criterion=friedman_mse, learning_rate=0.1, max_depth=3, min_samples_leaf=1, min_samples_split=2, n_estimators=10;, score=0.808 total time=   0.0s
[CV 1/5] END criterion=friedman_mse, learning_rate=0.1, max_depth=3, min_samples_leaf=1, min_samples_split=2, n_estimators=20;, score=0.949

In [27]:
GB = GradientBoostingRegressor(criterion = 'mse', learning_rate = 0.1, max_depth = 4, min_samples_leaf = 1, min_samples_split = 10, n_estimators = 800)
cv = cross_val_score(GB, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

GB.fit(X_train, y_train)
y_pred = GB.predict(X_test)
print(GB.score(X_test, y_test))
print(mean_squared_error(y_test, y_pred))

[0.99870442 0.99872247 0.99877915 0.99857351 0.99894413] mean:  0.9987447361279627
0.9990167996926319
0.0009652076948948942


### Xgboost

In [24]:
kf5 = KFold(n_splits = 5, shuffle = True)
XG_param = {'n_estimators' : [10, 50, 100, 150, 200, 500, 800], 
            'learning_rate' : [0.1, 0.01],
             'max_depth': [3, 4, 5, 10, None]}

XG = XGBRegressor()
XG_cv = GridSearchCV(XG, XG_param, cv = kf5, refit=True, verbose=3)
XG_cv.fit(X_train, y_train)
print(XG_cv.best_score_)
print(XG_cv.best_params_)

Fitting 5 folds for each of 70 candidates, totalling 350 fits
[CV 1/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.788 total time=   0.2s
[CV 2/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.769 total time=   0.0s
[CV 3/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.802 total time=   0.0s
[CV 4/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.779 total time=   0.0s
[CV 5/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.778 total time=   0.0s
[CV 1/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.989 total time=   0.0s
[CV 2/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.988 total time=   0.0s
[CV 3/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.992 total time=   0.0s
[CV 4/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.990 total time=   0.0s
[CV 5/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.991 total time=   0.0

In [28]:
XG = XGBRegressor(learning_rate = 0.1, max_depth = 4, n_estimators = 800)
cv = cross_val_score(XG, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

XG.fit(X_train, y_train)
y_pred = XG.predict(X_test)
print(XG.score(X_test, y_test))
print(mean_squared_error(y_test, y_pred))

[0.99851195 0.99867151 0.9987369  0.99836092 0.99863848] mean:  0.9985839521034169
0.9989776037236869
0.001003686375740532


### LGB

In [25]:
kf5 = KFold(n_splits = 5, shuffle = True)
LG_param = {'n_estimators' : [10, 50, 100, 150, 200, 500, 800], 
            'learning_rate' : [0.1, 0.01],
             'max_depth': [3, 4, 5, 10, -1]}

LG = LGBMRegressor()
LG_cv = GridSearchCV(LG, LG_param, cv = kf5, refit=True, verbose=3)
LG_cv.fit(X_train, y_train)
print(LG_cv.best_score_)
print(LG_cv.best_params_)

Fitting 5 folds for each of 70 candidates, totalling 350 fits
[CV 1/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.823 total time=   0.0s
[CV 2/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.813 total time=   0.0s
[CV 3/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.820 total time=   0.0s
[CV 4/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.813 total time=   0.0s
[CV 5/5] END learning_rate=0.1, max_depth=3, n_estimators=10;, score=0.807 total time=   0.0s
[CV 1/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.988 total time=   0.1s
[CV 2/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.987 total time=   0.0s
[CV 3/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.988 total time=   0.0s
[CV 4/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.986 total time=   0.0s
[CV 5/5] END learning_rate=0.1, max_depth=3, n_estimators=50;, score=0.988 total time=   0.0

In [29]:
LG = LGBMRegressor(learning_rate = 0.1, max_depth = -1, n_estimators = 150)
cv = cross_val_score(LG, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

LG.fit(X_train, y_train)
y_pred = LG.predict(X_test)
print(LG.score(X_test, y_test))
print(mean_squared_error(y_test, y_pred))

[0.98774871 0.99138865 0.99663839 0.9970319  0.99450938] mean:  0.9934634063427408
0.9971286252001752
0.0028188285041703494


### Neural Network

In [26]:
kf5 = KFold(n_splits = 5, shuffle = True)
NN_param = {'learning_rate': ['constant', 'invscaling', 'adaptive'],
            'hidden_layer_sizes': [(3,), (5,), (10,), (3,3), (5,5), (10,10)],
            'activation': ["logistic", "relu", "Tanh"]}

NN = MLPRegressor()
NN_cv = GridSearchCV(NN, NN_param, cv = kf5, refit=True, verbose=3)
NN_cv.fit(X_train, y_train)
print(NN_cv.best_score_)
print(NN_cv.best_params_)

Fitting 5 folds for each of 54 candidates, totalling 270 fits
[CV 1/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.624 total time=   0.3s
[CV 2/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.750 total time=   0.2s
[CV 3/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.831 total time=   0.2s
[CV 4/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.888 total time=   0.2s
[CV 5/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.877 total time=   0.2s
[CV 1/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=invscaling;, score=0.897 total time=   0.2s
[CV 2/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=invscaling;, score=0.771 total time=   0.2s
[CV 3/5] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=invscaling;, score=0.919 total time=   0.2s
[CV 4/5] END

In [31]:
NN = MLPRegressor(activation = 'relu', hidden_layer_sizes = (10,10), learning_rate = 'adaptive')
cv = cross_val_score(NN, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

NN.fit(X_train, y_train)
y_pred = NN.predict(X_test)
print(NN.score(X_test, y_test))
print(mean_squared_error(y_test, y_pred))

[0.98870788 0.99407682 0.99024073 0.99069754 0.99139394] mean:  0.9910233837540222
0.9913166521881573
0.008524442133134497


### Summary Result

In [32]:
regressions = [LinearRegression(),
               DecisionTreeRegressor(criterion = 'absolute_error', max_depth = 18, min_samples_leaf = 1, min_samples_split = 2, splitter = 'random'),
               RandomForestRegressor(criterion = 'mse', max_depth = None, min_samples_leaf = 1, min_samples_split = 2, n_estimators = 100),
               GradientBoostingRegressor(criterion = 'mse', learning_rate = 0.1, max_depth = 4, min_samples_leaf = 1, min_samples_split = 10, n_estimators = 800),
               XGBRegressor(learning_rate = 0.1, max_depth = 4, n_estimators = 800),
               LGBMRegressor(learning_rate = 0.1, max_depth = -1, n_estimators = 150),
               MLPRegressor(activation = 'relu', hidden_layer_sizes = (10,10), learning_rate = 'adaptive')
               ]

In [33]:
r2 = []
mse = []

for regression in regressions:
    regression.fit(X_train, y_train)
    y_pred = regression.predict(X_test)
    r2.append(r2_score(y_test, y_pred))
    mse.append(mean_squared_error(y_test, y_pred))

In [35]:
models = pd.DataFrame({'Model': ['Linear Regression','Decision Tree', 'Random Forest', 
                                 'Gradient Boosting Tree', 'Xgboost', 'LGB', 'Neural Network'],
                       'r2':r2,
                       'mse':mse})
models.sort_values(by='r2', ascending=False)

Model        r2       mse
3  Gradient Boosting Tree  0.999017  0.000965
4                 Xgboost  0.998978  0.001004
5                     LGB  0.997129  0.002819
2           Random Forest  0.995516  0.004402
6          Neural Network  0.989980  0.009837
1           Decision Tree  0.988593  0.011198
0       Linear Regression  0.911395  0.086984

## Classificatin Models

In [58]:
X_train, X_test, y_train, y_test = train_test_split(X_z, y_BS, test_size = .2, random_state = 20)

### Logistic Regression

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
log_param = {'penalty' : ['l1','l2'], 
             'C': np.logspace(-3,3,7),
             'solver'  : ['newton-cg', 'lbfgs', 'liblinear']}

log = LogisticRegression()
log_cv = GridSearchCV(log, log_param, cv = kf5, refit=True, verbose=3)
log_cv.fit(X_train, y_train)
print(log_cv.best_score_)
print(log_cv.best_params_)

In [59]:
log = LogisticRegression(C = 10, penalty = 'l1', solver= 'liblinear')
cv = cross_val_score(log, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

log.fit(X_train, y_train)
y_pred = log.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(log.score(X_test, y_test))

[0.90671642 0.89925373 0.93283582 0.94029851 0.92910448] mean:  0.9216417910447762
[[170  19]
 [ 15 131]]
              precision    recall  f1-score   support

           0       0.92      0.90      0.91       189
           1       0.87      0.90      0.89       146

    accuracy                           0.90       335
   macro avg       0.90      0.90      0.90       335
weighted avg       0.90      0.90      0.90       335

0.8985074626865671


### Random Forest

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
rf_param = {'max_depth': np.arange(2, 11),
            'min_samples_leaf': [1, 2, 4],
            'min_samples_split': [2, 5, 10],
            'n_estimators': np.arange(50, 201, 50)}

param = {'alpha':np.arange(0,1,0.1)}

rf = RandomForestClassifier()
rf_cv = GridSearchCV(rf, rf_param, cv=kf5, refit=True, verbose=3) 
rf_cv.fit(X_train, y_train)
print(rf_cv.best_score_)
print(rf_cv.best_params_)

In [60]:
rf = RandomForestClassifier(max_depth= 9, min_samples_leaf= 2, min_samples_split= 5, n_estimators= 200)
cv = cross_val_score(rf, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

rf.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(rf.score(X_test, y_test))

[0.95149254 0.94402985 0.94402985 0.94029851 0.90671642] mean:  0.9373134328358208
[[170  19]
 [ 12 134]]
              precision    recall  f1-score   support

           0       0.93      0.90      0.92       189
           1       0.88      0.92      0.90       146

    accuracy                           0.91       335
   macro avg       0.90      0.91      0.91       335
weighted avg       0.91      0.91      0.91       335

0.9074626865671642


### Gradient Boosting

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
gb_param = {
    "learning_rate": [0.001, 0.01, 0.1],
    'max_depth': [2, 5, 10],
    'min_samples_leaf': [1, 2, 4],
    'min_samples_split': [2, 5, 10],
    "n_estimators":[10, 100]
    }

gb = GradientBoostingClassifier()
gb_cv = GridSearchCV(gb, gb_param, cv=kf5, refit=True, verbose=3) 
gb_cv.fit(X_train, y_train)
print(gb_cv.best_score_)
print(gb_cv.best_params_)

In [61]:
gb = GradientBoostingClassifier(learning_rate=0.1, max_depth= 5, min_samples_leaf= 2, min_samples_split= 2, 
                                n_estimators= 100)
cv = cross_val_score(gb, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

gb.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(gb.score(X_test, y_test))

[0.94402985 0.88432836 0.94029851 0.96641791 0.94776119] mean:  0.9365671641791046
[[170  19]
 [ 12 134]]
              precision    recall  f1-score   support

           0       0.93      0.90      0.92       189
           1       0.88      0.92      0.90       146

    accuracy                           0.91       335
   macro avg       0.90      0.91      0.91       335
weighted avg       0.91      0.91      0.91       335

0.9164179104477612


### SVM

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
svm_param = {'C': [0.1, 1, 10, 100, 1000],  
             'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
             'kernel': ['rbf']}

svm = SVC()
svm_cv = GridSearchCV(svm, svm_param, cv=kf5, refit=True, verbose=3) 
svm_cv.fit(X_train, y_train)
print(svm_cv.best_score_)
print(svm_cv.best_params_)

In [62]:
svm = SVC(C=1000, gamma=0.001, kernel='rbf')
cv = cross_val_score(svm, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

svm.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(svm.score(X_test, y_test))

[0.89179104 0.93283582 0.96268657 0.92537313 0.91044776] mean:  0.9246268656716417
[[170  19]
 [ 12 134]]
              precision    recall  f1-score   support

           0       0.93      0.90      0.92       189
           1       0.88      0.92      0.90       146

    accuracy                           0.91       335
   macro avg       0.90      0.91      0.91       335
weighted avg       0.91      0.91      0.91       335

0.9014925373134328


### Xgboost

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
kb_param = {'min_child_weight': [1, 5, 10],
          'gamma': [0.5, 1, 1.5, 2, 5],
          'subsample': [0.6, 0.8, 1.0],
          'colsample_bytree': [0.6, 0.8, 1.0],
          'max_depth': [3, 4, 5]}

kb = XGBClassifier()
kb_cv = GridSearchCV(kb, kb_param, cv=kf5, refit=True, verbose=3) 
kb_cv.fit(X_train, y_train)
print(kb_cv.best_score_)
print(kb_cv.best_params_)

In [63]:
kb = XGBClassifier(colsample_bytree = 1.0, gamma = 2, max_depth = 3, min_child_weight = 1, subsample = 0.8)
cv = cross_val_score(kb, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

kb.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(kb.score(X_test, y_test))

[0.92164179 0.91791045 0.96268657 0.94029851 0.95149254] mean:  0.9388059701492537
[[170  19]
 [ 12 134]]
              precision    recall  f1-score   support

           0       0.93      0.90      0.92       189
           1       0.88      0.92      0.90       146

    accuracy                           0.91       335
   macro avg       0.90      0.91      0.91       335
weighted avg       0.91      0.91      0.91       335

0.9313432835820895


### KNN

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
knn_param = {'n_neighbors': [3, 4, 5, 6, 7, 8, 9, 10, 11, 12]}

knn = KNeighborsClassifier()
knn_cv = GridSearchCV(knn, knn_param, cv=kf5, refit=True, verbose=3) 
knn_cv.fit(X_train, y_train)
print(knn_cv.best_score_)
print(knn_cv.best_params_)

In [64]:
knn = KNeighborsClassifier(n_neighbors = 7)
cv = cross_val_score(knn, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

knn.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(knn.score(X_test, y_test))

[0.92910448 0.91791045 0.92164179 0.91044776 0.94029851] mean:  0.9238805970149253
[[170  19]
 [ 12 134]]
              precision    recall  f1-score   support

           0       0.93      0.90      0.92       189
           1       0.88      0.92      0.90       146

    accuracy                           0.91       335
   macro avg       0.90      0.91      0.91       335
weighted avg       0.91      0.91      0.91       335

0.9134328358208955


### Neural Network

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
nn_param = {'learning_rate': ["constant", "invscaling", "adaptive"],
            'hidden_layer_sizes': [(100,1), (100,2), (100,3)],
            'activation': ["logistic", "relu", "Tanh"]}

nn = MLPClassifier()
nn_cv = GridSearchCV(nn, nn_param, cv=kf5, refit=True, verbose=3) 
nn_cv.fit(X_train, y_train)
print(nn_cv.best_score_)
print(nn_cv.best_params_)

In [65]:
nn = MLPClassifier(activation = 'logistic', hidden_layer_sizes = (100, 2), learning_rate = 'invscaling')
cv = cross_val_score(nn, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

nn.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(nn.score(X_test, y_test))

[0.90671642 0.92537313 0.92537313 0.91791045 0.93656716] mean:  0.9223880597014926
[[170  19]
 [ 12 134]]
              precision    recall  f1-score   support

           0       0.93      0.90      0.92       189
           1       0.88      0.92      0.90       146

    accuracy                           0.91       335
   macro avg       0.90      0.91      0.91       335
weighted avg       0.91      0.91      0.91       335

0.9044776119402985


### Decision Tree

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
dt_param = {'max_depth': np.arange(2, 11),
            'min_samples_leaf': [1, 2, 4],
            'min_samples_split': [2, 5, 10]}

dt = DecisionTreeClassifier()
dt_cv = GridSearchCV(dt, dt_param, cv=kf5, refit=True, verbose=3) 
dt_cv.fit(X_train, y_train)
print(dt_cv.best_score_)
print(dt_cv.best_params_)

In [66]:
dt = DecisionTreeClassifier(max_depth = 9, min_samples_leaf = 1, min_samples_split = 2)
cv = cross_val_score(dt, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

dt.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(dt.score(X_test, y_test))

[0.92164179 0.89179104 0.91044776 0.93656716 0.91044776] mean:  0.914179104477612
[[170  19]
 [ 12 134]]
              precision    recall  f1-score   support

           0       0.93      0.90      0.92       189
           1       0.88      0.92      0.90       146

    accuracy                           0.91       335
   macro avg       0.90      0.91      0.91       335
weighted avg       0.91      0.91      0.91       335

0.9134328358208955


### LGB

In [ ]:
kf5 = StratifiedKFold(n_splits = 5, shuffle = True)
lgb_param = {'max_depth': np.arange(2, 11),
            'n_estimators': np.arange(50, 201, 50),
            'lambda_l1': [0, 1, 1.5],
            'lambda_l2': [0, 1]}

LGB = lgb.LGBMClassifier()
lgb_cv = GridSearchCV(LGB, lgb_param, cv=kf5, refit=True, verbose=3) 
lgb_cv.fit(X_train, y_train)
print(lgb_cv.best_score_)
print(lgb_cv.best_params_)

In [67]:
LGB = lgb.LGBMClassifier(lambda_l1=0, lambda_l2=1, max_depth=9, n_estimators=200)
cv = cross_val_score(LGB, X_train, y_train, cv = kf5)
print(cv, 'mean: ', cv.mean())

LGB.fit(X_train, y_train)
y_pred = rf.predict(X_test)
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))
print(LGB.score(X_test, y_test))

[LightGBM] [Warning] lambda_l2 is set=1, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] lambda_l2 is set=1, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] lambda_l2 is set=1, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [W

### Summary Result

In [68]:
classifiers = [LogisticRegression(C = 10, penalty = 'l1', solver= 'liblinear'),
               KNeighborsClassifier(n_neighbors=7),
               SVC(C=1000, gamma=0.001, kernel='rbf'),
               DecisionTreeClassifier(max_depth=9, min_samples_leaf=1, min_samples_split=2),
               RandomForestClassifier(max_depth=9, min_samples_leaf=2, min_samples_split=5, n_estimators=200),
               GradientBoostingClassifier(learning_rate=0.1, max_depth=5, min_samples_leaf=2,
                                          min_samples_split=2, n_estimators=100),
               MLPClassifier(activation='logistic', hidden_layer_sizes=(100, 2), learning_rate='invscaling'),
               XGBClassifier(colsample_bytree=1.0, gamma=2, max_depth=3, min_child_weight=1, subsample=0.8),
               lgb.LGBMClassifier(lambda_l1=0, lambda_l2=1, max_depth=9, n_estimators=200)]

In [69]:
acc = []
pre = []
rec = []
f1 = []

for classifier in classifiers:
    classifier.fit(X_train, y_train)
    y_pred = classifier.predict(X_test)
    acc.append(accuracy_score(y_test, y_pred))
    pre.append(precision_score(y_test, y_pred, average='weighted'))
    rec.append(recall_score(y_test, y_pred, average='weighted'))
    f1.append(f1_score(y_test, y_pred, average='weighted'))

[LightGBM] [Warning] lambda_l2 is set=1, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).


In [70]:
models = pd.DataFrame({'Model': ['Logistic Regression','KNN', 'SVM', 'Decision Tree', 'Random Forest', 
                                 'Gradient Boosting','Neural Network','Xgboost', 'LGB'],
                       'Accuracy':acc,
                       'Precision':pre,
                       'Recall':rec,
                       'F1':f1})
models.sort_values(by='Accuracy', ascending=False)

Model  Accuracy  Precision    Recall        F1
7              Xgboost  0.931343   0.931643  0.931343  0.931418
8                  LGB  0.919403   0.920577  0.919403  0.919586
5    Gradient Boosting  0.916418   0.917890  0.916418  0.916629
1                  KNN  0.913433   0.913515  0.913433  0.913466
3        Decision Tree  0.913433   0.913769  0.913433  0.913527
4        Random Forest  0.910448   0.911394  0.910448  0.910627
6       Neural Network  0.907463   0.908187  0.907463  0.907621
2                  SVM  0.901493   0.901430  0.901493  0.901453
0  Logistic Regression  0.895522   0.895894  0.895522  0.895636

# Method 2

## Regression Models

### Linear Model

In [13]:
kf10 = KFold(n_splits = 10, shuffle = True)

LR = LinearRegression()
cv = cross_val_score(LR, X_z, y_z, cv = kf10)
LR_r2 = cv.mean()
print(cv, 'mean: ', cv.mean())

[0.90548347 0.91161399 0.91303623 0.92683556 0.88457222 0.90050634
 0.91689702 0.91991828 0.90570804 0.90743737] mean:  0.9092008512235961


### Decision Tree

In [15]:
kf10 = KFold(n_splits = 10, shuffle = True)
DT_param = {'criterion' : ['squared_error','friedman_mse','absolute_error','poisson'], 
            'splitter' : ['best','random'],
             'max_depth': [2, 4, 5, 10, None],
             'min_samples_split'  : [2,5,10,20,50],
             'min_samples_leaf'  : [1,5,10]}

DT = DecisionTreeRegressor()
DT_cv = GridSearchCV(DT, DT_param, cv = kf10, refit=True, verbose=3)
DT_cv.fit(X_z, y_z)
DT_r2 = DT_cv.best_score_
DT_best_parm = DT_cv.best_params_
print(DT_cv.best_score_)
print(DT_cv.best_params_)

Fitting 10 folds for each of 600 candidates, totalling 6000 fits
[CV 1/10] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.817 total time=   0.0s
[CV 2/10] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.828 total time=   0.0s
[CV 3/10] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.815 total time=   0.0s
[CV 4/10] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.813 total time=   0.0s
[CV 5/10] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.785 total time=   0.0s
[CV 6/10] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, splitter=best;, score=0.823 total time=   0.0s
[CV 7/10] END criterion=squared_error, max_depth=2, min_samples_leaf=1, min_samples_split=2, sp

### Random Forest

In [16]:
kf10 = KFold(n_splits = 10, shuffle = True)
RF_param = {'n_estimators' : [100, 150, 200], 
            'criterion': ['mse', 'mae', 'poisson'],
             'max_depth': [2, 4, 5, 10, None],
             'min_samples_split'  : [2,5,10,20],
             'min_samples_leaf'  : [1,5,10]}

RF = RandomForestRegressor()
RF_cv = GridSearchCV(RF, RF_param, cv = kf10, refit=True, verbose=3)
RF_cv.fit(X_z, y_z)
RF_r2 = RF_cv.best_score_
RF_best_parm = RF_cv.best_params_
print(RF_cv.best_score_)
print(RF_cv.best_params_)

Fitting 10 folds for each of 540 candidates, totalling 5400 fits
[CV 1/10] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.848 total time=   0.1s
[CV 2/10] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.858 total time=   0.1s
[CV 3/10] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.817 total time=   0.1s
[CV 4/10] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.818 total time=   0.1s
[CV 5/10] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.818 total time=   0.1s
[CV 6/10] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.807 total time=   0.1s
[CV 7/10] END criterion=mse, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.843 total time=   0.1s
[CV 

### Gradient Boosting Tree

In [15]:
kf10 = KFold(n_splits = 10, shuffle = True)
GB_param = {'n_estimators' : [100, 150, 200, 500, 800], 
            'learning_rate' : [0.1, 0.01],
            'criterion' : ['friedman_mse', 'mse', 'mae'],
             'max_depth': [2, 4, 5, 10, None],
             'min_samples_split'  : [2,5,10],
             'min_samples_leaf'  : [1,5,10]}

GB = GradientBoostingRegressor()
GB_cv = GridSearchCV(GB, GB_param, cv = kf10, refit=True, verbose=3)
GB_cv.fit(X_z, y_z)
GB_r2 = GB_cv.best_score_
GB_best_parm = GB_cv.best_params_
print(GB_cv.best_score_)
print(GB_cv.best_params_)

Fitting 10 folds for each of 1350 candidates, totalling 13500 fits
[CV 1/10] END criterion=friedman_mse, learning_rate=0.1, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.992 total time=   0.1s
[CV 2/10] END criterion=friedman_mse, learning_rate=0.1, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.992 total time=   0.0s
[CV 3/10] END criterion=friedman_mse, learning_rate=0.1, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.991 total time=   0.0s
[CV 4/10] END criterion=friedman_mse, learning_rate=0.1, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.991 total time=   0.0s
[CV 5/10] END criterion=friedman_mse, learning_rate=0.1, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;, score=0.992 total time=   0.0s
[CV 6/10] END criterion=friedman_mse, learning_rate=0.1, max_depth=2, min_samples_leaf=1, min_samples_split=2, n_estimators=100;

### XGBoost

In [16]:
kf10 = KFold(n_splits = 10, shuffle = True)
XG_param = {'n_estimators' : [100, 150, 200, 500, 800], 
            'learning_rate' : [0.1, 0.01],
             'max_depth': [2, 4, 5, 10, None]}

XG = XGBRegressor()
XG_cv = GridSearchCV(XG, XG_param, cv = kf10, refit=True, verbose=3)
XG_cv.fit(X_z, y_z)
XG_r2 = XG_cv.best_score_
XG_best_parm = XG_cv.best_params_
print(XG_cv.best_score_)
print(XG_cv.best_params_)

Fitting 10 folds for each of 50 candidates, totalling 500 fits
[CV 1/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.990 total time=   0.1s
[CV 2/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.991 total time=   0.0s
[CV 3/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.991 total time=   0.0s
[CV 4/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.991 total time=   0.0s
[CV 5/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.993 total time=   0.0s
[CV 6/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.991 total time=   0.0s
[CV 7/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.989 total time=   0.0s
[CV 8/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.992 total time=   0.0s
[CV 9/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.992 total time=   0.0s
[CV 10/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0

### LGB

In [17]:
kf10 = KFold(n_splits = 10, shuffle = True)
LG_param = {'n_estimators' : [100, 150, 200, 500], 
            'learning_rate' : [0.1, 0.01],
             'max_depth': [2, 4, 5, 10, -1]}

LG = LGBMRegressor()
LG_cv = GridSearchCV(LG, LG_param, cv = kf10, refit=True, verbose=3)
LG_cv.fit(X_z, y_z)
LG_r2 = LG_cv.best_score_
LG_best_parm = LG_cv.best_params_
print(LG_cv.best_score_)
print(LG_cv.best_params_)

Fitting 10 folds for each of 40 candidates, totalling 400 fits
[CV 1/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.987 total time=   0.1s
[CV 2/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.992 total time=   0.0s
[CV 3/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.989 total time=   0.0s
[CV 4/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.990 total time=   0.0s
[CV 5/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.990 total time=   0.0s
[CV 6/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.993 total time=   0.0s
[CV 7/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.989 total time=   0.0s
[CV 8/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.989 total time=   0.0s
[CV 9/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0.990 total time=   0.0s
[CV 10/10] END learning_rate=0.1, max_depth=2, n_estimators=100;, score=0

### Neural Network

In [19]:
kf10 = KFold(n_splits = 10, shuffle = True)
NN_param = {'learning_rate': ['constant', 'invscaling', 'adaptive'],
            'hidden_layer_sizes': [(3,), (5,), (10,), (3,3), (5,5), (10,10)],
            'activation': ["logistic", "relu", "Tanh"]}

NN = MLPRegressor()
NN_cv = GridSearchCV(NN, NN_param, cv = kf10, refit=True, verbose=3)
NN_cv.fit(X_z, y_z)
NN_r2 = NN_cv.best_score_
NN_best_parm = NN_cv.best_params_
print(NN_cv.best_score_)
print(NN_cv.best_params_)

Fitting 10 folds for each of 54 candidates, totalling 540 fits
[CV 1/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.826 total time=   0.5s
[CV 2/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.971 total time=   0.3s
[CV 3/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.966 total time=   0.3s
[CV 4/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.812 total time=   0.3s
[CV 5/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.975 total time=   0.3s
[CV 6/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.979 total time=   0.3s
[CV 7/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.810 total time=   0.3s
[CV 8/10] END activation=logistic, hidden_layer_sizes=(3,), learning_rate=constant;, score=0.955 total time=   0.3s
[CV 9/10]

### Summary Result

In [37]:
models = pd.DataFrame({'Model': ['Linear Regression','Decision Tree', 'Random Forest', 
                                 'Gradient Boosting Tree', 'Xgboost', 'LGB', 'Neural Network'],
                       'parm': ['', DT_best_parm, RF_best_parm, GB_best_parm, XG_best_parm, LG_best_parm, NN_best_parm],
                       'r2':[LR_r2, DT_r2, RF_r2, GB_r2, XG_r2, LG_r2, NN_r2]})
models.sort_values(by='r2', ascending=False).reset_index(drop = True)

Model                                               parm  \
0  Gradient Boosting Tree  {'criterion': 'friedman_mse', 'learning_rate':...   
1                 Xgboost  {'learning_rate': 0.1, 'max_depth': 4, 'n_esti...   
2           Random Forest  {'criterion': 'mae', 'max_depth': None, 'min_s...   
3                     LGB  {'learning_rate': 0.1, 'max_depth': -1, 'n_est...   
4           Decision Tree  {'criterion': 'squared_error', 'max_depth': No...   
5          Neural Network  {'activation': 'relu', 'hidden_layer_sizes': (...   
6       Linear Regression                                                      

         r2  
0  0.999218  
1  0.999163  
2  0.996511  
3  0.995700  
4  0.992638  
5  0.992423  
6  0.909201

# Predict Test data

In [38]:
GB_best_parm

{'criterion': 'friedman_mse',
 'learning_rate': 0.1,
 'max_depth': 4,
 'min_samples_leaf': 1,
 'min_samples_split': 5,
 'n_estimators': 800}

In [58]:
test_data = pd.read_csv('option_test_wolabel.csv')

In [40]:
test_data.head()

S    K       tau        r
0  431.618600  460  0.293651  0.03147
1  432.633296  420  0.182540  0.03147
2  432.633296  430  0.182540  0.03147
3  431.618600  415  0.293651  0.03147
4  434.772855  420  0.043651  0.03147

Scale test data

In [51]:
X_test_scale = stdx.transform(test_data)

Train the model with the best parameter and all training data set

In [56]:
GB_use = GradientBoostingRegressor(
    criterion = 'friedman_mse',
    learning_rate = 0.1,
    max_depth = 4,
    min_samples_leaf = 1,
    min_samples_split = 5,
    n_estimators = 800)
GB_use.fit(X_z,y_z)
y_pred_z = GB_use.predict(X_test_scale)

In [57]:
y_pred_z

array([-1.00258729,  0.23357713, -0.29194575, ..., -1.02217196,
        0.64974084,  0.03854654])

Transform value back to unscaled data

In [60]:
y_pred = stdy.inverse_transform(y_pred_z.reshape(-1,1))

In [61]:
test_data['value'] = y_pred

In [62]:
test_data

S    K       tau        r      value
0     431.618600  460  0.293651  0.03147   1.022340
1     432.633296  420  0.182540  0.03147  18.376628
2     432.633296  430  0.182540  0.03147  10.998907
3     431.618600  415  0.293651  0.03147  23.960517
4     434.772855  420  0.043651  0.03147  15.552473
...          ...  ...       ...      ...        ...
1115  440.067417  435  0.182540  0.02962  11.895176
1116  439.081203  485  0.293651  0.02962   0.458435
1117  439.081203  475  0.293651  0.02962   0.747394
1118  442.490015  420  0.043651  0.02962  24.219074
1119  440.067417  430  0.182540  0.02962  15.638629

[1120 rows x 5 columns]

In [63]:
test_data.to_csv('test_data_pred.csv')